In [1]:
import sys
from time import sleep
from selenium import webdriver
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.webdriver.common.by import By
from selenium.webdriver.common.keys import Keys
from selenium.common.exceptions import NoSuchElementException

import pandas as pd
import numpy as np

In [2]:
TIMEOUT = 5

driver = None

In [3]:
df = pd.read_csv('../../data/ulsan_rest_title.csv', encoding='utf-8-sig')


In [4]:
def search_review(driver, df, index, p_name):
  place = []
  user = []
  rating = []
  comment = []
  enter = False
  # 장소를 검색했을 때 바로 장소가 뜨지 않고 관련 장소 여러개 나올 때
  try:
    #관련 장소 여러개
    info_list = driver.find_element(By.CSS_SELECTOR, '#QA0Szd > div > div > div.w6VYqd > div.bJzME.tTVLSc > div > div.e07Vkf.kA9KIf > div > div > div.m6QErb.DxyBCb.kA9KIf.dS8AEf.ecceSd > div.m6QErb.DxyBCb.kA9KIf.dS8AEf.ecceSd').find_elements(By.CSS_SELECTOR, 'div.Nv2PK.THOPZb.CpccDe')
    
    #관련 장소 여러개 태그가 다른 경우
    if len(info_list) == 0:
      info_list = driver.find_element(By.CSS_SELECTOR, '#QA0Szd > div > div > div.w6VYqd > div.bJzME.tTVLSc > div > div.e07Vkf.kA9KIf > div > div > div.m6QErb.DxyBCb.kA9KIf.dS8AEf.ecceSd > div.m6QErb.DxyBCb.kA9KIf.dS8AEf.ecceSd').find_elements(By.CSS_SELECTOR, 'div.Nv2PK.Q2HXcd.THOPZb')
    
    #카카오맵에서 가져온 장소 이름으로 관련 장소 여러개에서 찾는 부분
    for info in info_list:
      if df.loc[index, 'title'] in info.find_element(By.CSS_SELECTOR, 'div.qBF1Pd.fontHeadlineSmall').text:
        info.find_element(By.XPATH, '..').click()
        enter = True
        break
      else:
        continue
    #관련 장소를 찾았을 때
    if enter == True:
      try:
        #리뷰 보는 곳 클릭
        driver.find_element(By.CSS_SELECTOR, 'div.PPCwl').click()
        
        #리뷰 모아놓은 박스 위치
        elem = driver.find_element(By.CSS_SELECTOR, '#QA0Szd > div > div > div.w6VYqd > div.bJzME.tTVLSc > div > div.e07Vkf.kA9KIf > div > div > div.m6QErb.DxyBCb.kA9KIf.dS8AEf')
        
        review_count = driver.find_element(By.CSS_SELECTOR, '#QA0Szd > div > div > div.w6VYqd > div.bJzME.tTVLSc > div > div.e07Vkf.kA9KIf > div > div > div.m6QErb.DxyBCb.kA9KIf.dS8AEf > div.PPCwl > div > div.jANrlb > div.fontBodySmall').text.replace('리뷰 ', '').replace('개', '')
        
        #리뷰 개수가 1000개가 넘어가면 1,000이런 식으로 표시
        if ',' in review_count:
          review_count = review_count.replace(',', '')
          
        review_count = int(review_count)
          
        if review_count >= 200:
          review_count = 200
        
        #리뷰 스크롤
        for i in range(review_count//5):
          driver.execute_script("arguments[0].scrollBy(0, 5000)", elem)
          sleep(0.5)
      
        review_boxes = driver.find_elements(By.CSS_SELECTOR, '#QA0Szd > div > div > div.w6VYqd > div.bJzME.tTVLSc > div > div.e07Vkf.kA9KIf > div > div > div.m6QErb.DxyBCb.kA9KIf.dS8AEf > div:nth-child(9) > div')
        
        if len(review_boxes) <review_count:
          review_boxes = driver.find_elements(By.CSS_SELECTOR, '#QA0Szd > div > div > div.w6VYqd > div.bJzME.tTVLSc > div > div.e07Vkf.kA9KIf > div > div > div.m6QErb.DxyBCb.kA9KIf.dS8AEf > div:nth-child(8) > div')
          
        if review_count<200:
          for i in range(0, (review_count)*3, 3):
            print('p_name: ', p_name)
            place.append(p_name)
            
            user_name = review_boxes[i].find_element(By.CSS_SELECTOR, 'div.WNxzHc.qLhwHc > a > div.d4r55 > span').text
            print('user_name: ', user_name)
            user.append(user_name)
          
            # 평점이 별일때
            place_rating = int(review_boxes[i].find_element(By.CSS_SELECTOR, 'span.kvMYJc').get_attribute('aria-label').replace('별표 ', '').replace('개', ''))
            #평점이 몇/몇일 때
            # place_rating = int(review_boxes[i].find_element(By.CSS_SELECTOR, 'span.fzvQIb').text.replace('/5', ''))
            print('place_rating: ', place_rating)
            rating.append(place_rating)
          
            #커멘트 둘 중 하나
            # place_comment = review_boxes[i].find_element(By.CSS_SELECTOR, 'div.GHT2ce > span.wiI7pd').text
            place_comment = review_boxes[i].find_element(By.CSS_SELECTOR, 'div.MyEned > span.wiI7pd').text
            print('place_comment: ', place_comment)
            comment.append(place_comment)
            
          review_df = pd.DataFrame({
              'place_id':place,
              'user_id':user,
              'score':rating,
              'comment':comment
          },)
          
          try:
            old_review_df = pd.read_csv(f'./kakao_reviews/restaruant/review/{p_name}.csv', encoding='utf-8-sig')
            review_df = pd.concat([review_df, old_review_df])
          except:
            pass

          review_df.to_csv(f'./kakao_reviews/restaruant/review/{p_name}.csv', index = False, header=True, encoding='utf-8-sig')
          return f'./restaruant/{p_name}.csv'
          
        else:
          for i in range(0, 200*3, 3):
            print('p_name: ', p_name)
            place.append(p_name)
            
            user_name = review_boxes[i].find_element(By.CSS_SELECTOR, 'div.WNxzHc.qLhwHc > a > div.d4r55 > span').text
            print('user_name: ', user_name)
            user.append(user_name)
          
            # 평점이 별일때
            place_rating = int(review_boxes[i].find_element(By.CSS_SELECTOR, 'span.kvMYJc').get_attribute('aria-label').replace('별표 ', '').replace('개', ''))
            #평점이 몇/몇일 때
            # place_rating = int(review_boxes[i].find_element(By.CSS_SELECTOR, 'span.fzvQIb').text.replace('/5', ''))
            print('place_rating: ', place_rating)
            rating.append(place_rating)
          
            #커멘트 둘 중 하나
            # place_comment = review_boxes[i].find_element(By.CSS_SELECTOR, 'div.GHT2ce > span.wiI7pd').text
            place_comment = review_boxes[i].find_element(By.CSS_SELECTOR, 'div.MyEned > span.wiI7pd').text
            print('place_comment: ', place_comment)
            comment.append(place_comment)
            
          review_df = pd.DataFrame({
              'place_id':place,
              'user_id':user,
              'score':rating,
              'comment':comment
          },)
          
          try:
            old_review_df = pd.read_csv(f'./kakao_reivews/restaruant/review/{p_name}.csv', encoding='utf-8-sig')
            review_df = pd.concat([review_df, old_review_df])
          except:
            pass

          review_df.to_csv(f'./kakao_reviews/restaruant/review/{p_name}.csv', index = False, header=True, encoding='utf-8-sig')
          return f'./restaruant/{p_name}.csv'
          
      except Exception as e:
        print(e)
        return '리뷰 없음'
    
    else:
      return '리뷰 없음'

  except Exception as e:
    try:
      driver.find_element(By.CSS_SELECTOR, 'div.PPCwl').click()
      
      elem = driver.find_element(By.CSS_SELECTOR, '#QA0Szd > div > div > div.w6VYqd > div.bJzME.tTVLSc > div > div.e07Vkf.kA9KIf > div > div > div.m6QErb.DxyBCb.kA9KIf.dS8AEf')
      
      review_count = driver.find_element(By.CSS_SELECTOR, '#QA0Szd > div > div > div.w6VYqd > div.bJzME.tTVLSc > div > div.e07Vkf.kA9KIf > div > div > div.m6QErb.DxyBCb.kA9KIf.dS8AEf > div.PPCwl > div > div.jANrlb > div.fontBodySmall').text.replace('리뷰 ', '').replace('개', '')
      
      if ',' in review_count:
        review_count = review_count.replace(',', '')
        
      review_count = int(review_count)
          
      if review_count >= 200:
        review_count = 200
      
      for i in range(review_count//5):
        driver.execute_script("arguments[0].scrollBy(0, 5000)", elem)
        sleep(0.5)
      
      review_boxes = driver.find_elements(By.CSS_SELECTOR, '#QA0Szd > div > div > div.w6VYqd > div.bJzME.tTVLSc > div > div.e07Vkf.kA9KIf > div > div > div.m6QErb.DxyBCb.kA9KIf.dS8AEf > div:nth-child(8) > div')
      
      if len(review_boxes) < review_count:
        review_boxes = driver.find_elements(By.CSS_SELECTOR, '#QA0Szd > div > div > div.w6VYqd > div.bJzME.tTVLSc > div > div.e07Vkf.kA9KIf > div > div > div.m6QErb.DxyBCb.kA9KIf.dS8AEf > div:nth-child(9) > div')
      
      print(len(review_boxes))
      
      if review_count<200:
        for i in range(0, (review_count)*3, 3):
          print('p_name: ', p_name)
          place.append(p_name)
            
          user_name = review_boxes[i].find_element(By.CSS_SELECTOR, 'div.WNxzHc.qLhwHc > a > div.d4r55 > span').text
          print('user_name: ', user_name)
          user.append(user_name)
          
          # 평점이 별일때
          place_rating = int(review_boxes[i].find_element(By.CSS_SELECTOR, 'span.kvMYJc').get_attribute('aria-label').replace('별표 ', '').replace('개', ''))
          #평점이 몇/몇일 때
          # place_rating = int(review_boxes[i].find_element(By.CSS_SELECTOR, 'span.fzvQIb').text.replace('/5', ''))
          print('place_rating: ', place_rating)
          rating.append(place_rating)
          
          #커멘트 둘 중 하나
          # place_comment = review_boxes[i].find_element(By.CSS_SELECTOR, 'div.GHT2ce > span.wiI7pd').text
          place_comment = review_boxes[i].find_element(By.CSS_SELECTOR, 'div.MyEned > span.wiI7pd').text
          print('place_comment: ', place_comment)
          comment.append(place_comment)
            
        review_df = pd.DataFrame({
            'place_id':place,
            'user_id':user,
            'score':rating,
            'comment':comment
        },)
        
        try:
          old_review_df = pd.read_csv(f'./kakao_reviews/restaruant/review/{p_name}.csv', encoding='utf-8-sig')
          review_df = pd.concat([review_df, old_review_df])
        except:
          pass

        review_df.to_csv(f'./kakao_reviews/restaruant/review/{p_name}.csv', index = False, header=True, encoding='utf-8-sig')
        return f'./restaruant/{p_name}.csv'
          
      else:
        for i in range(0, 200*3, 3):
          print('p_name: ', p_name)
          place.append(p_name)
            
          user_name = review_boxes[i].find_element(By.CSS_SELECTOR, 'div.WNxzHc.qLhwHc > a > div.d4r55 > span').text
          print('user_name: ', user_name)
          user.append(user_name)
          
          # 평점이 별일때
          place_rating = int(review_boxes[i].find_element(By.CSS_SELECTOR, 'span.kvMYJc').get_attribute('aria-label').replace('별표 ', '').replace('개', ''))
          #평점이 몇/몇일 때
          # place_rating = int(review_boxes[i].find_element(By.CSS_SELECTOR, 'span.fzvQIb').text.replace('/5', ''))
          print('place_rating: ', place_rating)
          rating.append(place_rating)
          
          #커멘트 둘 중 하나
          # place_comment = review_boxes[i].find_element(By.CSS_SELECTOR, 'div.GHT2ce > span.wiI7pd').text
          place_comment = review_boxes[i].find_element(By.CSS_SELECTOR, 'div.MyEned > span.wiI7pd').text
          print('place_comment: ', place_comment)
          comment.append(place_comment)
            
        review_df = pd.DataFrame({
            'place_id':place,
            'user_id':user,
            'score':rating,
            'comment':comment
        },)
        
        try:
          old_review_df = pd.read_csv(f'./kakao_reviews/restaruant/review/{p_name}.csv', encoding='utf-8-sig')
          review_df = pd.concat([review_df, old_review_df])
        except:
          pass

        review_df.to_csv(f'./kakao_reviews/restaruant/review/{p_name}.csv', index = False, header=True, encoding='utf-8-sig')
        return f'./kakao_reviews/restaruant/review/{p_name}.csv'
          
    except Exception as e:
      print(e)
      return '리뷰 없음'

In [5]:
for search in range(495):
  Options = webdriver.ChromeOptions()
  user_agent = 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/111.0.0.0 Safari/537.36'

  Options.add_argument('user-agent=' + user_agent)

  driver = webdriver.Chrome("./chromedriver", options=Options)

  driver.get("https://www.google.co.kr/maps")
  driver.implicitly_wait(TIMEOUT)
  elem = driver.find_element(By.ID, "searchboxinput")
  # elem.send_keys(df.loc[search_index[i], 'p_category']+' '+df.loc[search_index[i], 'p_name'])
  elem.send_keys('울산 '+df.loc[search, 'title'])
  # 검색 단추를 누른다
  elem = driver.find_element(By.ID, "searchbox-searchbutton")
  elem.click()
  name = df.loc[search, 'title']
  
  search_review(driver, df, search, name)
  
  driver.quit()

C:\Users\Lenovo\AppData\Local\Temp\ipykernel_4560\3682438401.py:7: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  driver = webdriver.Chrome("./chromedriver", options=Options)


317
p_name:  상무초밥 울산삼산점
user_name:  고릴라 Gorilla
place_rating:  5
place_comment:  울산 현대백화점 맞은편에 위치한 상무초밥 울산삼산점 입니다.
재료가 신선하고 초밥도 너무 맛있습니다.
직원분들모두 친절하고 매장도 청결하고 넓습니다.…
p_name:  상무초밥 울산삼산점
user_name:  보노보노
place_rating:  5
place_comment:  가격대비 가성비 좋은곳같아요 맛도 좋고
점심특선B를 먹었는데 초밥에 온메밀국수에 튀김에 디저트까지 나오더군요 온메밀국수는
내 취향이 아니었네요
밑반찬도 백김치와 양파토마토절임이 나왔는데 맛있었어요
p_name:  상무초밥 울산삼산점
user_name:  류종범
place_rating:  5
place_comment:  맛있었습니다. 흰살생선들이 특히 마음에 들더라구요 다만 소고기 초밥의 식감 조금 아쉬웠지만 그런데로 맛있었습니다. 모밀을 서비스로 주시는데 생각한거보다 양이 적긴했지만 정말 탱탱하고 맛있습니다.
p_name:  상무초밥 울산삼산점
user_name:  guy electric
place_rating:  4
place_comment:  이곳에 고객대하는 수준은 정말 저렴하네요. 주문한 것 맘대로 삭제해서 못 먹은 메뉴도 있네요.모듬회는 이런저런 맛을 느낄 수 있어 좋았네요. 초밥은 맛있는데 간혹 와사비가 많이 들어 간 것이 있네요. 뒷편에 서일주차장에 주차하라해서 주차했더니, 500원 할인해주네요. 참. 전체적으로 괜찮지만 직원들 응대는 너무 형편 없군요
p_name:  상무초밥 울산삼산점
user_name:  이성곤
place_rating:  4
place_comment:  어린이날 방문했는데 사람많아서  웨이팅20분
초등학생있을시 50%할인 깜짝놀람
가게내부아주 깨끗하고 생각보다 홀이 넓음…
p_name:  상무초밥 울산삼산점
user_name:  IM K
place_rating:  4
place_comment:  기본으로 주는 미

C:\Users\Lenovo\AppData\Local\Temp\ipykernel_4560\3682438401.py:7: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  driver = webdriver.Chrome("./chromedriver", options=Options)


Message: element not interactable
  (Session info: chrome=111.0.5563.110)
Stacktrace:
Backtrace:
	(No symbol) [0x009437D3]
	(No symbol) [0x008D8B81]
	(No symbol) [0x007DB230]
	(No symbol) [0x0080E337]
	(No symbol) [0x00803253]
	(No symbol) [0x0082B41C]
	(No symbol) [0x00802B96]
	(No symbol) [0x0082B774]
	(No symbol) [0x00841215]
	(No symbol) [0x0082B216]
	(No symbol) [0x00800D97]
	(No symbol) [0x0080253D]
	GetHandleVerifier [0x00BBABF2+2510930]
	GetHandleVerifier [0x00BE8EC1+2700065]
	GetHandleVerifier [0x00BEC86C+2714828]
	GetHandleVerifier [0x009F3480+645344]
	(No symbol) [0x008E0FD2]
	(No symbol) [0x008E6C68]
	(No symbol) [0x008E6D4B]
	(No symbol) [0x008F0D6B]
	BaseThreadInitThunk [0x768300F9+25]
	RtlGetAppContainerNamedObjectPath [0x77347BBE+286]
	RtlGetAppContainerNamedObjectPath [0x77347B8E+238]

77
p_name:  세비로
user_name:  Juhyeon Park
place_rating:  3
place_comment:  엔티크한 감성으로 잘 카페는 꾸민 것 같아요. 주문하고 옷 수선하는 곳 가서 구경할 수도 있고, 2층도 있어서 독립적으로 잘 놀 수 있는 곳 같아요. 하지만 나오는 음식은 별로 같아요. 디저트로 나오는

C:\Users\Lenovo\AppData\Local\Temp\ipykernel_4560\3682438401.py:7: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  driver = webdriver.Chrome("./chromedriver", options=Options)


...

Message: no such element: Unable to locate element: {"method":"css selector","selector":"div.PPCwl"}
  (Session info: chrome=111.0.5563.110)
Stacktrace:
Backtrace:
	(No symbol) [0x009437D3]
	(No symbol) [0x008D8B81]
	(No symbol) [0x007DB36D]
	(No symbol) [0x0080D382]
	(No symbol) [0x0080D4BB]
	(No symbol) [0x00843302]
	(No symbol) [0x0082B464]
	(No symbol) [0x00841215]
	(No symbol) [0x0082B216]
	(No symbol) [0x00800D97]
	(No symbol) [0x0080253D]
	GetHandleVerifier [0x00BBABF2+2510930]
	GetHandleVerifier [0x00BE8EC1+2700065]
	GetHandleVerifier [0x00BEC86C+2714828]
	GetHandleVerifier [0x009F3480+645344]
	(No symbol) [0x008E0FD2]
	(No symbol) [0x008E6C68]
	(No symbol) [0x008E6D4B]
	(No symbol) [0x008F0D6B]
	BaseThreadInitThunk [0x768300F9+25]
	RtlGetAppContainerNamedObjectPath [0x77347BBE+286]
	RtlGetAppContainerNamedObjectPath [0x77347B8E+238]

239
p_name:  시그너스커피바
user_name:  이나경
place_rating:  4
place_comment:  추천받아서 갔다왔습니다. 드립커피 온두라스로 먹었구요. 산미가 좋았습니다. 시그널라테도 맛있게 먹었습니다. 라떼 진하고 맛났어요
p_n

C:\Users\Lenovo\AppData\Local\Temp\ipykernel_4560\3682438401.py:7: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  driver = webdriver.Chrome("./chromedriver", options=Options)


197
p_name:  러프로스터스
user_name:  킹알짱드리드
place_rating:  5
place_comment:  버스창문을 보다가 무심코 눈이 갔던 가게. 집 돌아가는 길에 방문했고 깔끔한 내부, 정갈한 인테리어 그리고 가격 대비 정말 훌륭한 커피까지. 큰 창문으로 얼핏 보이는 강을 보고 있으면 다음에 또 오고 싶다는 생각이 드는 가게였다.
울산을 방문한다면 꼭 한 번쯤은 방문해보길!
p_name:  러프로스터스
user_name:  Sun L
place_rating:  5
place_comment:  아파트앞 상가에 위치하고있고
주차는 바로 뒷편에 가능합니다
(현재 아파트주민분들과 주차관계로 조율중이신것같으셨어요…
p_name:  러프로스터스
user_name:  따로
place_rating:  4
place_comment:  주차장만 아니라면 완벽한 카페.
분위기 깔끔하고 커피는 취향껏 원두 선택이 가능 합니다.
바리스타는 추출에 굉장히 신경을 쓰는 듯 했고,…
p_name:  러프로스터스
user_name:  Somin Kang
place_rating:  5
place_comment:  비오는날 방문했었는데, 운치있고 너무 좋았어요. 커피맛도 좋구요- 의자가 푹신하거나 편한 의자는 아니라서 걸터앉아 마시긴하지만 적당히 즐기며 맛있는 커피를 잘마시고 왔습니다.
p_name:  러프로스터스
user_name:  차미림
place_rating:  4
place_comment:  네비 치고 가니 자꾸 아파트에서 멈춰서...ㅋ 도로 앞쪽에서 스타더스트? 찾으면 찾기 쉬움 커피는 라떼만 주로 마시는데 대박~
커피맛은 진한데 엄청 부드러운 맛
굿입니다~
p_name:  러프로스터스
user_name:  민돌이
place_rating:  5
place_comment:  너무너무좋아요 커피도맛있고 쿠키도맛있고 분위기도 매우만족
p_name:  러프로스터스
user_name:  Hyunkyung Cho
place_rating:  5
place_comment

C:\Users\Lenovo\AppData\Local\Temp\ipykernel_4560\3682438401.py:7: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  driver = webdriver.Chrome("./chromedriver", options=Options)


293
p_name:  유정호선장집
user_name:  고릴라 Gorilla
place_rating:  4
place_comment:  맛있게 잘 먹었습니다. 하지만 서빙하시는 아주머니~~~
교육은 많이 필요 할것같습니다.
p_name:  유정호선장집
user_name:  이정화
place_rating:  4
place_comment:  왜 유명한지 알겠어요
일단 킹크랩가격은 서울보다 조금 싸거나 큰차이 없어요 다만 킹크랩 살이 제대로 올라서 퀄리티 👍
거기다가 찌는 시간도 적당하고 먹기 좋게 손질하는건 정말 최고 👍 👍 👍 기다리는 시간동안 서빙하는 회, 킹크랩 튀김은 센스있네요 차림비는…
p_name:  유정호선장집
user_name:  안은세
place_rating:  5
place_comment:  너무너무 맛있어요♡ 대게 살 꽉~차있어요.
갠적으로 매운탕 정~말 맛있었답니다.
오늘 마침 운 좋게도 식당 직원분 생일이셔서 생크림 케이크 맛있게 먹었어요ㅎㅎ…
p_name:  유정호선장집
user_name:  한바다
place_rating:  5
place_comment:  울산 정자항에서 가장 유명한 대게전문점
기장, 포항, 강릉, 속초 등에서 대게집을 가보아도 개인적으로 여기만큼 코스로 푸짐하게 내어주는 곳을 보지는 못한거 같아요.
코스로 다양하게 먹을 수 있어서 좋고 맛도 좋구~~
p_name:  유정호선장집
user_name:  이선희
place_rating:  2
place_comment:  키로에 5~6만원짜리 정자대게를 먹으러갔는뎅
간시간이 아까워서
그냥 러시아산 박달대게 키로 9만원 짜리만 있어서…
p_name:  유정호선장집
user_name:  sang Il kim
place_rating:  4
place_comment:  전화예약하면 10%할인된다고해서 예약하고 갔음. 박달대게 1kg 9만원에서 10%  할인받음. 어른4명가서 3kg먹었음. 코스로 먹고 게밥과 게라면까지 먹었음. 정말 배불리 먹고 대게의 맛에 취했음. 다리는 일부 튀김

In [6]:
df.to_csv('kakaoGoogle.csv', encoding='utf-8-sig')